In [9]:
import dspy
from dspy.predict import Retry
from dspy.primitives.assertions import assert_transform_module, backtrack_handler
import importlib

importlib.reload(dspy)

# Configure the AzureOpenAI language model
azure_turbo = dspy.AzureOpenAI(api_base='https://bionlp-gpt4-wang.openai.azure.com/', api_key="a494edc84d714b6c8a12e7212974b793", api_version='2024-03-01-preview', model='gpt-35-turbo')
dspy.settings.configure(lm=azure_turbo)

In [21]:
import re

def eval_metric(true, prediction, trace=None):
    try:
        pred = prediction.answer
        matches = re.findall(r"\([A-D]\)", pred)
        parsed_answer = matches[-1] if matches else ""
        return parsed_answer == true.answer
    except:
        return False 

In [22]:
class GenerateAnswer(dspy.Signature):
    """You are a helpful medical expert, and your task is to answer a multi-choice medical question. Please first think step-by-step and then choose the answer from the provided options."""
    
    question = dspy.InputField(desc="Question")
    options = dspy.InputField(desc="Answer choice options")
    answer = dspy.OutputField(desc="You should respond with one of (A), (B), (C), or (D)")

In [23]:
class AnswerQuestion(dspy.Module):
    def __init__(self):
        super().__init__()
        self.generate_answer = dspy.ChainOfThought(GenerateAnswer)
    
    def forward(self, question, options):
        response = self.generate_answer(question=question, options=options)
      
        #valid_response = "(A)" in response.answer or "(B)" in response.answer or "(C)" in response.answer or "(D)" in response.answer  

        #dspy.Assert(valid_response, "You must respond with one of (A), (B), (C), or (D) as part of your answer.")

        return dspy.Prediction(answer=response.answer)

In [24]:
import json

train_data = []
val_data = []
test_data = []

with open("/Users/khandekarns/Downloads/data_clean/questions/US/4_options/phrases_no_exclude_train.jsonl") as file:
    for line in file:
        qa_info = json.loads(line)
        train_data.append(qa_info)
        

with open("/Users/khandekarns/Downloads/data_clean/questions/US/4_options/phrases_no_exclude_dev.jsonl") as file:
    for line in file:
        qa_info = json.loads(line)
        val_data.append(qa_info)


with open("/Users/khandekarns/Downloads/data_clean/questions/US/4_options/phrases_no_exclude_test.jsonl") as file:
    for line in file:
        qa_info = json.loads(line)
        test_data.append(qa_info)

In [25]:
import json


def get_instances(file_path):

    items = []

    with open(file_path) as file:
        indices = json.load(file)

    if "train" in file_path:
        dataset = train_data

    if "test" in file_path:
        dataset = test_data 

    if "val" in file_path:
        dataset = val_data 
    
    for index in indices:
        index = int(index)

        items.append(dataset[index])
    
    return items


train_data = get_instances("/Users/khandekarns/Documents/DSPy/eligible_notes/medqa_train_eligible.json")
val_data = get_instances("/Users/khandekarns/Documents/DSPy/eligible_notes/medqa_val_eligible.json")
test_data = get_instances("/Users/khandekarns/Documents/DSPy/eligible_notes/medqa_test_eligible.json")

In [15]:
# Only pass in the valid ones and save this to a jsonl file 

with open("/Users/khandekarns/Documents/MedQA_GPT35/train.jsonl", 'w') as file:
    for dictionary in train_data:
        # Convert the dictionary to a JSON string and write it to the file
        json_line = json.dumps(dictionary)
        file.write(json_line + '\n')


with open("/Users/khandekarns/Documents/MedQA_GPT35/val.jsonl", 'w') as file:
    for dictionary in val_data:
        # Convert the dictionary to a JSON string and write it to the file
        json_line = json.dumps(dictionary)
        file.write(json_line + '\n')


with open("/Users/khandekarns/Documents/MedQA_GPT35/test.jsonl", 'w') as file:
    for dictionary in test_data:
        # Convert the dictionary to a JSON string and write it to the file
        json_line = json.dumps(dictionary)
        file.write(json_line + '\n')

In [26]:
def question_with_options(options):

   return "\n(A) " + options['A'] + "\n(B) " + options['B'] +  "\n(C) " + options['C'] + "\n(D) " + options['D']


def generate_dspy_examples(dataset):

   examples = []
   
   for i in range(len(dataset)):
      options = question_with_options(dataset[i]['options'])
      
      example = dspy.Example({"question": dataset[i]['question'], "options": options, "answer": "(" + dataset[i]["answer_idx"] + ")"}).with_inputs("question", "options") 

      examples.append(example)

   return examples 


train_dspy_examples = generate_dspy_examples(train_data)
val_dspy_examples = generate_dspy_examples(val_data)
test_dspy_examples = generate_dspy_examples(test_data)

In [27]:
from dspy.evaluate import Evaluate

evaluate_test = Evaluate(devset=test_dspy_examples, metric=eval_metric, num_threads=6, display_progress=True, display_table=True)

In [28]:
evaluate_test(AnswerQuestion())

Average Metric: 168 / 263  (63.9):  21%|██        | 263/1270 [02:19<05:34,  3.01it/s]  INFO:backoff:Backing off request(...) for 0.1s (openai.RateLimitError: Error code: 429 - {'error': {'code': '429', 'message': 'Requests to the ChatCompletions_Create Operation under Azure OpenAI API version 2024-03-01-preview have exceeded token rate limit of your current OpenAI S0 pricing tier. Please retry after 1 second. Please go here: https://aka.ms/oai/quotaincrease if you would like to further increase the default rate limit.'}})


Backing off 0.1 seconds after 1 tries calling function <function AzureOpenAI.request at 0x117bd6b60> with kwargs {}


Average Metric: 240 / 377  (63.7):  30%|██▉       | 377/1270 [03:16<11:13,  1.33it/s]  INFO:backoff:Backing off request(...) for 0.4s (openai.RateLimitError: Error code: 429 - {'error': {'code': '429', 'message': 'Requests to the ChatCompletions_Create Operation under Azure OpenAI API version 2024-03-01-preview have exceeded token rate limit of your current OpenAI S0 pricing tier. Please retry after 1 second. Please go here: https://aka.ms/oai/quotaincrease if you would like to further increase the default rate limit.'}})


Backing off 0.4 seconds after 1 tries calling function <function AzureOpenAI.request at 0x117bd6b60> with kwargs {}


Average Metric: 245 / 384  (63.8):  30%|███       | 384/1270 [03:18<04:56,  2.99it/s]INFO:backoff:Backing off request(...) for 0.5s (openai.RateLimitError: Error code: 429 - {'error': {'code': '429', 'message': 'Requests to the ChatCompletions_Create Operation under Azure OpenAI API version 2024-03-01-preview have exceeded token rate limit of your current OpenAI S0 pricing tier. Please retry after 1 second. Please go here: https://aka.ms/oai/quotaincrease if you would like to further increase the default rate limit.'}})


...

Backing off 0.7 seconds after 1 tries calling function <function AzureOpenAI.request at 0x117bd6b60> with kwargs {}


Average Metric: 733 / 1185  (61.9):  93%|█████████▎| 1185/1270 [09:47<00:32,  2.61it/s]INFO:backoff:Backing off request(...) for 0.2s (openai.RateLimitError: Error code: 429 - {'error': {'code': '429', 'message': 'Requests to the ChatCompletions_Create Operation under Azure OpenAI API version 2024-03-01-preview have exceeded token rate limit of your current OpenAI S0 pricing tier. Please retry after 1 second. Please go here: https://aka.ms/oai/quotaincrease if you would like to further increase the default rate limit.'}})


Backing off 0.2 seconds after 1 tries calling function <function AzureOpenAI.request at 0x117bd6b60> with kwargs {}


Average Metric: 785 / 1270  (61.8): 100%|██████████| 1270/1270 [10:34<00:00,  2.00it/s]


61.81

In [29]:
from tqdm import tqdm
from dspy.teleprompt import BootstrapFewShotWithRandomSearch

tqdm._instances.clear()

config = dict(max_bootstrapped_demos=5, max_labeled_demos=0, num_candidate_programs=20, num_threads=6)
teleprompter = BootstrapFewShotWithRandomSearch(metric = eval_metric, **config)
optimized = teleprompter.compile(AnswerQuestion(), trainset=train_dspy_examples, valset=val_dspy_examples)

Going to sample between 1 and 5 traces per predictor.
Will attempt to bootstrap 20 candidate sets.


Average Metric: 210 / 324  (64.8):  26%|██▌       | 324/1269 [02:42<21:59,  1.40s/it]

Backing off 0.7 seconds after 1 tries calling function <function AzureOpenAI.request at 0x117bd6b60> with kwargs {}


Average Metric: 241 / 368  (65.5):  29%|██▉       | 368/1269 [03:02<11:17,  1.33it/s]INFO:backoff:Backing off request(...) for 0.7s (openai.RateLimitError: Error code: 429 - {'error': {'code': '429', 'message': 'Requests to the ChatCompletions_Create Operation under Azure OpenAI API version 2024-03-01-preview have exceeded token rate limit of your current OpenAI S0 pricing tier. Please retry after 1 second. Please go here: https://aka.ms/oai/quotaincrease if you would like to further increase the default rate limit.'}})


Backing off 0.7 seconds after 1 tries calling function <function AzureOpenAI.request at 0x117bd6b60> with kwargs {}


...

Backing off 0.6 seconds after 1 tries calling function <function AzureOpenAI.request at 0x117bd6b60> with kwargs {}
Backing off 0.6 seconds after 1 tries calling function <function AzureOpenAI.request at 0x117bd6b60> with kwargs {}


Average Metric: 847.0 / 1257  (67.4):  99%|█████████▉| 1256/1269 [10:03<00:12,  1.06it/s]INFO:backoff:Backing off request(...) for 2.6s (openai.RateLimitError: Error code: 429 - {'error': {'code': '429', 'message': 'Requests to the ChatCompletions_Create Operation under Azure OpenAI API version 2024-03-01-preview have exceeded token rate limit of your current OpenAI S0 pricing tier. Please retry after 1 second. Please go here: https://aka.ms/oai/quotaincrease if you would like to further increase the default rate limit.'}})


Backing off 2.6 seconds after 3 tries calling function <function AzureOpenAI.request at 0x117bd6b60> with kwargs {}


Average Metric: 857.0 / 1269  (67.5): 100%|██████████| 1269/1269 [10:09<00:00,  2.08it/s]

Score: 67.53 for set: [1]
Scores so far: [65.96, 65.96, 67.53, 69.42, 67.53, 67.06, 66.82, 65.33, 69.5, 68.64, 68.64, 65.96, 66.75, 68.79, 67.69, 67.22, 68.64, 67.38, 68.09, 69.74, 67.38, 64.38, 67.53]
Best score: 69.74
Average of max per entry across top 1 scores: 0.6973995271867612
Average of max per entry across top 2 scores: 0.7848699763593381
Average of max per entry across top 3 scores: 0.8242710795902285
Average of max per entry across top 5 scores: 0.8620961386918834
Average of max per entry across top 8 scores: 0.8873128447596532
Average of max per entry across top 9999 scores: 0.9511426319936959
23 candidate programs found.


In [30]:
evaluate_test(optimized)

Average Metric: 21 / 28  (75.0):   2%|▏         | 28/1270 [00:09<06:46,  3.06it/s]

Backing off 0.1 seconds after 1 tries calling function <function AzureOpenAI.request at 0x117bd6b60> with kwargs {}


Average Metric: 24 / 31  (77.4):   2%|▏         | 31/1270 [00:11<10:21,  1.99it/s]INFO:backoff:Backing off request(...) for 0.6s (openai.RateLimitError: Error code: 429 - {'error': {'code': '429', 'message': 'Requests to the ChatCompletions_Create Operation under Azure OpenAI API version 2024-03-01-preview have exceeded token rate limit of your current OpenAI S0 pricing tier. Please retry after 1 second. Please go here: https://aka.ms/oai/quotaincrease if you would like to further increase the default rate limit.'}})


Backing off 0.6 seconds after 1 tries calling function <function AzureOpenAI.request at 0x117bd6b60> with kwargs {}


Average Metric: 25 / 33  (75.8):   3%|▎         | 33/1270 [00:12<11:05,  1.86it/s]/opt/anaconda3/envs/dspy_repo/lib/python3.12/site-packages/joblib/_store_backends.py:215: CacheWarning: Unable to cache to disk. Possibly a race condition in the creation of the directory. Exception: [Errno 2] No such file or directory: '/Users/khandekarns/cachedir_joblib/joblib/dsp/modules/azure_openai/v1_chat_request/<locals>/v1_cached_gpt3_turbo_request_v2_wrapped/<locals>/v1_cached_gpt3_turbo_request_v2/73d305578df3789828c2720550436ad1/output.pkl.thread-5811496112-pid-34106' -> '/Users/khandekarns/cachedir_joblib/joblib/dsp/modules/azure_openai/v1_chat_request/<locals>/v1_cached_gpt3_turbo_request_v2_wrapped/<locals>/v1_cached_gpt3_turbo_request_v2/73d305578df3789828c2720550436ad1/output.pkl'.
  warnings.warn(
Average Metric: 41 / 56  (73.2):   4%|▍         | 56/1270 [00:20<07:04,  2.86it/s]INFO:backoff:Backing off request(...) for 0.5s (openai.RateLimitError: Error code: 429 - {'error': {'code': '429

...

Backing off 0.1 seconds after 1 tries calling function <function AzureOpenAI.request at 0x117bd6b60> with kwargs {}


Average Metric: 850 / 1243  (68.4):  98%|█████████▊| 1243/1270 [10:00<00:16,  1.65it/s]

Backing off 0.7 seconds after 1 tries calling function <function AzureOpenAI.request at 0x117bd6b60> with kwargs {}


Average Metric: 866 / 1270  (68.2): 100%|██████████| 1270/1270 [10:12<00:00,  2.07it/s]


68.19

In [31]:
from dspy.teleprompt import MIPROv2
import random

random.seed(42)

#train_dspy_samples = random.sample(train_dspy_examples, 3000)
#val_dspy_samples = random.sample(val_dspy_examples, 300)

teleprompter = MIPROv2(prompt_model= azure_turbo, task_model=azure_turbo, metric=eval_metric, num_candidates=20, metric_threshold=None)
kwargs = dict(num_threads=3, display_progress=True, display_table=True)
compiled_prompt_opt = teleprompter.compile(AnswerQuestion(), trainset=train_dspy_examples, valset= val_dspy_examples, max_labeled_demos=0, max_bootstrapped_demos=5, eval_kwargs=kwargs, requires_permission_to_run=False)


Please be advised that based on the parameters you have set, the maximum number of LM calls is projected as follows:


- Prompt Model: 10 data summarizer calls + 20 * 1 lm calls in program + (2) lm calls in program aware proposer = 32 prompt model calls
- Task Model: 25 examples in minibatch * 30 batches + 10146 examples in train set * 3 full evals = 31188 task model calls

Estimated Cost Calculation:

Total Cost = (Number of calls to task model * (Avg Input Token Length per Call * Task Model Price per Input Token + Avg Output Token Length per Call * Task Model Price per Output Token) 
            + (Number of calls to prompt model * (Avg Input Token Length per Call * Task Prompt Price per Input Token + Avg Output Token Length per Call * Prompt Model Price per Output Token).

For a preliminary estimate of potential costs, we recommend you perform your own calculations based on the task
and prompt models you intend to use. If the projected costs exceed your budget or expectations, you 

INFO:backoff:Backing off request(...) for 0.6s (openai.BadRequestError: Error code: 400 - {'error': {'message': "This model's maximum context length is 4096 tokens. However, you requested 4364 tokens (3964 in the messages, 400 in the completion). Please reduce the length of the messages or completion.", 'type': 'invalid_request_error', 'param': 'messages', 'code': 'context_length_exceeded'}})


b: 70
Backing off 0.6 seconds after 1 tries calling function <function AzureOpenAI.request at 0x117bd6b60> with kwargs {'n': 1, 'temperature': 1.0}


INFO:backoff:Backing off request(...) for 1.2s (openai.BadRequestError: Error code: 400 - {'error': {'message': "This model's maximum context length is 4096 tokens. However, you requested 4364 tokens (3964 in the messages, 400 in the completion). Please reduce the length of the messages or completion.", 'type': 'invalid_request_error', 'param': 'messages', 'code': 'context_length_exceeded'}})


Backing off 1.2 seconds after 2 tries calling function <function AzureOpenAI.request at 0x117bd6b60> with kwargs {'n': 1, 'temperature': 1.0}


...




As a knowledgeable medical expert, approach the task of answering this multi-choice medical question systematically. Begin by carefully analyzing the question and considering each option provided. Consider the rationale behind each possible answer, and carefully evaluate the given information in order to make an informed decision. Select the answer that best aligns with the presented facts and thoughtfully reasoning through the options. As you formulate your response, keep in mind to clearly indicate your chosen answer as (A), (B), (C), or (D). Remember to follow a well-structured and detailed approach, taking into account the provided description and tips throughout the question analysis. Now proceed to answer the interactive medical question.

---

Follow the following format.

Question: Question

Options: Answer choice options

Reasoning: Let's think step by step in order to ${produce the answer}. We ...

Answer: You should respond with one of (A), (B), (C), or (D)

---

Question

Average Metric: 1 / 4  (25.0):   0%|          | 4/10146 [00:04<3:02:23,  1.08s/it] /opt/anaconda3/envs/dspy_repo/lib/python3.12/site-packages/joblib/_store_backends.py:215: CacheWarning: Unable to cache to disk. Possibly a race condition in the creation of the directory. Exception: [Errno 22] Invalid argument: '/Users/khandekarns/cachedir_joblib/joblib/dsp/modules/azure_openai/v1_chat_request/<locals>/v1_cached_gpt3_turbo_request_v2_wrapped/<locals>/v1_cached_gpt3_turbo_request_v2/a73f7bbd38468c1287809bba2073a933'.
  warnings.warn(
Average Metric: 838 / 1266  (66.2):  12%|█▏        | 1266/10146 [14:41<2:45:44,  1.12s/it]/opt/anaconda3/envs/dspy_repo/lib/python3.12/site-packages/joblib/_store_backends.py:215: CacheWarning: Unable to cache to disk. Possibly a race condition in the creation of the directory. Exception: [Errno 2] No such file or directory: '/Users/khandekarns/cachedir_joblib/joblib/dsp/modules/azure_openai/v1_chat_request/<locals>/v1_cached_gpt3_turbo_request_v2_wrapped/<l

UPDATING BEST SCORE WITH 64.89


Average Metric: 58 / 92  (63.0):   7%|▋         | 92/1269 [01:04<19:21,  1.01it/s]/opt/anaconda3/envs/dspy_repo/lib/python3.12/site-packages/joblib/_store_backends.py:215: CacheWarning: Unable to cache to disk. Possibly a race condition in the creation of the directory. Exception: [Errno 22] Invalid argument: '/Users/khandekarns/cachedir_joblib/joblib/dsp/modules/azure_openai/v1_chat_request/<locals>/v1_cached_gpt3_turbo_request_v2_wrapped/<locals>/v1_cached_gpt3_turbo_request_v2/b4de7eebf65db82697917bd4092d00be'.
  warnings.warn(
Average Metric: 78 / 125  (62.4):  10%|▉         | 125/1269 [01:23<10:36,  1.80it/s]/opt/anaconda3/envs/dspy_repo/lib/python3.12/site-packages/joblib/_store_backends.py:215: CacheWarning: Unable to cache to disk. Possibly a race condition in the creation of the directory. Exception: [Errno 22] Invalid argument: '/Users/khandekarns/cachedir_joblib/joblib/dsp/modules/azure_openai/v1_chat_request/<locals>/v1_cached_gpt3_turbo_request_v2_wrapped/<locals>/v1_cache

OSError: [Errno 22] Invalid argument: '/Users/khandekarns/cachedir_joblib/joblib/dsp/modules/azure_openai/v1_chat_request/<locals>/v1_cached_gpt3_turbo_request_v2_wrapped/<locals>/v1_cached_gpt3_turbo_request_v2/func_code.py'

In [ ]:
evaluate_test(optimized)

In [ ]:
evaluate_test(compiled_prompt_opt)

Average Metric: 40 / 59  (67.8):   5%|▍         | 59/1270 [00:19<08:02,  2.51it/s]INFO:backoff:Backing off request(...) for 0.8s (openai.RateLimitError: Error code: 429 - {'error': {'code': '429', 'message': 'Requests to the ChatCompletions_Create Operation under Azure OpenAI API version 2024-03-01-preview have exceeded token rate limit of your current OpenAI S0 pricing tier. Please retry after 1 second. Please go here: https://aka.ms/oai/quotaincrease if you would like to further increase the default rate limit.'}})


Backing off 0.8 seconds after 1 tries calling function <function AzureOpenAI.request at 0x116d52b60> with kwargs {}


Average Metric: 42 / 61  (68.9):   5%|▍         | 61/1270 [00:21<13:35,  1.48it/s]

Backing off 0.0 seconds after 1 tries calling function <function AzureOpenAI.request at 0x116d52b60> with kwargs {}


Average Metric: 42 / 64  (65.6):   5%|▌         | 64/1270 [00:22<10:25,  1.93it/s]INFO:backoff:Backing off request(...) for 0.7s (openai.RateLimitError: Error code: 429 - {'error': {'code': '429', 'message': 'Requests to the ChatCompletions_Create Operation under Azure OpenAI API version 2024-03-01-preview have exceeded token rate limit of your current OpenAI S0 pricing tier. Please retry after 1 second. Please go here: https://aka.ms/oai/quotaincrease if you would like to further increase the default rate limit.'}})


...

Backing off 1.0 seconds after 1 tries calling function <function AzureOpenAI.request at 0x116d52b60> with kwargs {}
Backing off 0.8 seconds after 1 tries calling function <function AzureOpenAI.request at 0x116d52b60> with kwargs {}
Backing off 0.5 seconds after 1 tries calling function <function AzureOpenAI.request at 0x116d52b60> with kwargs {}


Average Metric: 857 / 1243  (68.9):  98%|█████████▊| 1242/1270 [09:57<00:19,  1.46it/s]INFO:backoff:Backing off request(...) for 0.1s (openai.RateLimitError: Error code: 429 - {'error': {'code': '429', 'message': 'Requests to the ChatCompletions_Create Operation under Azure OpenAI API version 2024-03-01-preview have exceeded token rate limit of your current OpenAI S0 pricing tier. Please retry after 1 second. Please go here: https://aka.ms/oai/quotaincrease if you would like to further increase the default rate limit.'}})


Backing off 0.1 seconds after 2 tries calling function <function AzureOpenAI.request at 0x116d52b60> with kwargs {}


Average Metric: 875 / 1270  (68.9): 100%|██████████| 1270/1270 [10:11<00:00,  2.08it/s]


68.9